# [PySpark AI](https://github.com/databrickslabs/pyspark-ai)

```shell
mamba install -c plotly plotly
```

or

```
pip install pyspark-ai plotly-express
```

Clean data rows using:

```
tr -d '\r' < all_perth_310121.csv > all_perth_310121_new.csv
```

In [2]:
# import geofunctions as S
import pyspark.sql.functions as F
from langchain.chat_models import ChatOpenAI
from pyspark_ai import SparkAI
from pyspark.sql import SparkSession

In [3]:
spark = SparkSession.builder.appName("SparkAI").getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/08/03 07:22:07 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [1]:
# S.st_register_functions()

In [3]:
llm = ChatOpenAI(model_name="gpt-3.5-turbo", temperature=0)
spark_ai = SparkAI(llm, verbose=True)
spark_ai.activate()

In [4]:
schema = ",".join(
    [
        "`ADDRESS` string",
        "`SUBURB` string",
        "`PRICE` double",
        "`BEDROOMS` integer",
        "`BATHROOMS` integer",
        "`GARAGE` integer",
        "`LAND_AREA` double",
        "`FLOOR_AREA` double",
        "`BUILD_YEAR` int",
        "`CBD_DIST` double",
        "`NEAREST_STN` string",
        "`NEAREST_STN_DIST` string",
        "`DATE_SOLD` string",
        "`POSTCODE` string",
        "`LATITUDE` double",
        "`LONGITUDE` double",
        "`NEAREST_SCH` string",
        "`NEAREST_SCH_DIST` double",
        "`NEAREST_SCH_RANK` int",
    ]
)

In [5]:
df = spark.read.csv("data/all_perth_310121_new.csv", header=True, schema=schema).cache()

In [6]:
df.count()

33656

In [7]:
spark_ai.plot_df(
    df, "show distribution of NEAREST_SCH_DIST less than 8 miles in 32 bins"
)

INFO: import plotly.express as px
import pandas as pd

# Convert Spark DataFrame to Pandas DataFrame
df_pandas = df.toPandas()

# Filter the data where NEAREST_SCH_DIST is less than 8 miles
filtered_df = df_pandas[df_pandas['NEAREST_SCH_DIST'] < 8]

# Create the histogram plot
fig = px.histogram(filtered_df, x='NEAREST_SCH_DIST', nbins=32)

# Display the plot
fig.show()


In [8]:
df2 = spark_ai.transform_df(df, "with 3 bedrooms and 2 garages")

INFO: Creating temp view for the transform:
df.createOrReplaceTempView("spark_ai_temp_view_4cab64")

INFO: SQL query for the transform:
SELECT * FROM spark_ai_temp_view_4cab64 WHERE BEDROOMS = 3 AND GARAGE = 2


In [9]:
spark_ai.plot_df(
    df2,
    "show map of all locations using LONGITUDE and LATITUDE with only address column",
)

INFO: Here is the Python code to visualize the result of `df` using plotly:


```
import plotly.express as px
import pandas as pd

# Convert Spark DataFrame to Pandas DataFrame
df_pandas = df.toPandas()

# Create a scatter plot using longitude and latitude columns
fig = px.scatter_mapbox(df_pandas, lat="LATITUDE", lon="LONGITUDE", hover_name="ADDRESS")

# Set the mapbox access token (replace "YOUR_MAPBOX_ACCESS_TOKEN" with your own token)
fig.update_layout(mapbox_style="open-street-map", mapbox_accesstoken="YOUR_MAPBOX_ACCESS_TOKEN")

# Display the plot
fig.show()
```

Please note that you need to replace "YOUR_MAPBOX_ACCESS_TOKEN" with your own Mapbox access token. You can sign up for a free account on the Mapbox website to obtain an access token.

This code converts the Spark DataFrame `df` to a Pandas DataFrame `df_pandas` using the `toPandas()` method. Then, it creates a scatter plot using the longitude and latitude columns from the Pandas DataFrame. The `hover_name` parameter is s

In [ ]:
# spark_ai.transform_df(
#     df,
#     "Create regression model to calculate the price of the house using BEDROOMS,BATHROOMS and LAND_AREA",
# )

### Point Near Point Analysis.

In [ ]:
lhs = (
    spark.range(20)
    .withColumnRenamed("id", "id")
    .withColumn("lon", F.rand() * 360 - 180)
    .withColumn("lat", F.rand() * 180 - 90)
)

rhs = (
    spark.range(20)
    .withColumnRenamed("id", "id")
    .withColumn("lon", F.rand() * 360 - 180)
    .withColumn("lat", F.rand() * 180 - 90)
)

rhs.createOrReplaceTempView("rhs")

In [ ]:
res = spark_ai.transform_df(lhs, "find nearest rhs element to each row")

In [ ]:
# res.explain(extended=False)